[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/drive/15UUJKrBZCU2iZwyUeT95qL0A-5VbAVk-?usp=sharing)

#Get real data

In [ ]:
from tqdm import tqdm

In [ ]:
import pandas as pd

dataset = pd.read_csv('../../data/poetry_keywords.csv')

In [ ]:
dataset

text   
0     Влас Прогулкин —\nмилый мальчик,\nспать ложилс...  \
1     Засыпает на рассвете,\nскомкав\nёрзаньем\nкров...   
2     Разошлись\nдругие\nв школы,–\nВлас\nу крана\nп...   
3     Пошагал\nи встал разиней:\nвывеска на магазине...   
4     С конца прочёл\nзнаток наук, —\nНомисвыходит\n...   
...                                                 ...   
7750  Чудный сон мне бог послал—\nС длинной белой бо...   
7751  Бедный пахарь утомленный,\nОтрешишь волов от п...   
7752  И страшуся и надеюсь,\nКазни вечныя страшуся,\...   
7753  О нет, мне жизнь не надоела,\nЯ жить люблю, я ...   
7754  Еще хранятся наслажденья\nДля любопытства моег...   

                                               keywords      author  
0     ['спать', 'журнальчик', 'заставить', 'мальчик'...  Маяковский  
1     ['вставать', 'детвора', 'отец', 'засыпать', 'у...  Маяковский  
2     ['мочить', 'дрематься', 'выходить', 'школа', '...  Маяковский  
3     ['магазин', 'вывеска', 'прочесть', 'пошагать',...  Маяковский  
4     ['номисвыходить', 'наука', 'пять', 'прочесть',...  Маяковский  
...                                                 ...         ...  
7750  ['сон', 'старец', 'ангел', 'плаватель', 'готов...      Пушкин  
7751  ['утомлённый', 'сон', 'ждать', 'исповедовать',...      Пушкин  
7752  ['успокоить', 'надеяться', 'казнь', 'творец', ...      Пушкин  
7753  ['надоесть', 'охладеть', 'жизнь', 'хотеть', 'м...      Пушкин  
7754  ['наслаждение', 'воображение', 'сон', 'ещё', '...      Пушкин  

[7755 rows x 3 columns]

In [ ]:
authors = dataset['author'].unique()

In [ ]:
import torch
device = torch.device('cuda:0') if torch.cuda.is_available() else torch.device('cpu')

# medium model generation

In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM
path = 'AnyaSchen/rugpt3-medium-keywords2poetry'
tokenizer = AutoTokenizer.from_pretrained(path)
model = AutoModelForCausalLM.from_pretrained(path).to(device)

In [ ]:
def generate_poetry(input: str, model, num_beams=3):
  input = input if len(input) > 0 else tokenizer.bos_token #токен начала предложения
  input_ids = tokenizer.encode(input, return_tensors="pt").to(device)
  # Create an attention mask
  attention_mask = (input_ids != tokenizer.pad_token_id).float()

    # Set the pad_token_id
  tokenizer.pad_token_id = tokenizer.eos_token_id
  with torch.no_grad():
        out = model.generate(input_ids,
                            do_sample=True,
                            num_beams=num_beams,
                            temperature=2.0,
                            top_p=0.9,
                            max_length = 200,
                            # stopping_criteria=StoppingCriteriaList([stop_criteria]),
                            eos_token_id=tokenizer.eos_token_id,
                            bos_token_id=tokenizer.bos_token_id,
                            attention_mask=attention_mask
                            ).to(device)
  return tokenizer.batch_decode(out, skip_special_tokens=True)[0]

In [ ]:
inp = 'Автор: Маяковский\nКлючевые слова:'

In [ ]:
print(generate_poetry(inp, model))

Setting `pad_token_id` to `eos_token_id`:50259 for open-end generation.


Автор: Маяковский
Ключевые слова: германия, фашистский, гитлерюгенд, рабочий, стена
Поэзия: Слушайте,
рабочие мира,
злые языки утверждают, будто
в Германии
во время войны
вейсками
строился Ад.
Слушайте,
фашистские наймиты,
строители рая,
вопите, что все неправда!
Это неправда!
Это –
строился
рабочий мира
на Эльбе!



In [ ]:
dataset['keywords'] = dataset['keywords'].apply(lambda x: ', '.join(x.split("'")[1:-1:2]))

In [ ]:
generated_poetry = {author: [] for author in authors}

In [ ]:
for author in authors:
  print(f'Current author: {author}')
  data = dataset[dataset['author'] == author].reset_index()

  for i in tqdm(range(data.shape[0])):
    inp = f"Автор: {author}\nКлючевые слова: {data['keywords'][i]}"
    generated_poetry[author].append(generate_poetry(inp, model))

Current author: Маяковский


100%|█████████████████████████████████████████████████████████████████████████████| 1107/1107 [1:09:33<00:00,  3.77s/it]


Current author: Тютчев


100%|███████████████████████████████████████████████████████████████████████████████| 1000/1000 [51:38<00:00,  3.10s/it]


Current author: Блок


100%|█████████████████████████████████████████████████████████████████████████████| 1963/1963 [1:51:50<00:00,  3.42s/it]


Current author: Есенин


100%|█████████████████████████████████████████████████████████████████████████████| 1478/1478 [1:01:46<00:00,  2.51s/it]


Current author: Пушкин


100%|█████████████████████████████████████████████████████████████████████████████| 2207/2207 [1:53:09<00:00,  3.08s/it]


In [ ]:
import pickle

In [ ]:
def upload_generated_poetry(data: dict):
  file_name = './medium_all_poets.pkl'

  with open(file_name, 'wb') as f:
    pickle.dump(data, f)

In [ ]:
upload_generated_poetry(generated_poetry)

In [ ]:
del model

# large

In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM
path = 'AnyaSchen/rugpt3-large-keywords2poetry'
tokenizer = AutoTokenizer.from_pretrained(path)
model = AutoModelForCausalLM.from_pretrained(path).to(device)

In [ ]:
generated_poetry_large = {author: [] for author in authors}

In [ ]:
for author in authors:
  print(f'Current author: {author}')
  data = dataset[dataset['author'] == author].reset_index()

  for i in tqdm(range(data.shape[0])):
    inp = f"Автор: {author}\nКлючевые слова: {data['keywords'][i]}"
    generated_poetry_large[author].append(generate_poetry(inp, model))

Current author: Маяковский


  0%|                                                                                          | 0/1107 [00:00<?, ?it/s]/root/anaconda3/lib/python3.9/site-packages/transformers/generation/utils.py:1255: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation)
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:50259 for open-end generation.
100%|█████████████████████████████████████████████████████████████████████████████| 1107/1107 [1:08:07<00:00,  3.69s/it]


Current author: Тютчев


100%|███████████████████████████████████████████████████████████████████████████████| 1000/1000 [42:30<00:00,  2.55s/it]


Current author: Блок


100%|█████████████████████████████████████████████████████████████████████████████| 1963/1963 [1:35:47<00:00,  2.93s/it]


Current author: Есенин


100%|███████████████████████████████████████████████████████████████████████████████| 1478/1478 [53:42<00:00,  2.18s/it]


Current author: Пушкин


100%|█████████████████████████████████████████████████████████████████████████████| 2207/2207 [1:41:36<00:00,  2.76s/it]


In [ ]:
def upload_generated_poetry(data: dict):
  file_name = './large_all_poets.pkl'

  with open(file_name, 'wb') as f:
    pickle.dump(data, f)

In [ ]:
upload_generated_poetry(generated_poetry_large)